# 01. Import & Install Dependencies

In [1]:
!pip install tensorflow tensorflow-gpu opencv-python mediapipe sklearn matplotlib

In [1]:
import cv2                                # Computer Vison Library OpenCV
import numpy as np                        # numpy arrays structure our datasets (numpy instead of tensorflow)
import os                                 # work with operating systems file path
from matplotlib import pyplot as plt      # matplotlib just helps us visualize images a little bit easier
import mediapipe as mp                    # mediapipe (https://google.github.io/mediapipe/)
from math import *

# 02. Using Mediapipe (Google's open-source framework)

In [3]:
mp_face_mesh = mp.solutions.face_mesh              # FaceMesh Model has -- 478 -- Keypoints 
mp_drawing_styles = mp.solutions.drawing_styles    # Drawing styles
mp_drawing = mp.solutions.drawing_utils            # Drawing utilites

## Given the original image and obtaining the values through the model.

In [17]:
def mediapipe_detection(image,model):                 
    image = cv2.cvtColor(image , cv2.COLOR_BGR2RGB)   # COLOR CONVERSION BGR 2 RGB
    image.flags.writeable = False                     # Image is no longer writeable
    results = model.process(image)                    # Make prediction
    image.flags.writeable = True                      # Image is now writeable
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)    # COLOR CONVERSION RGB 2 BGR
    return image, results

## Storing the keypoints values in the mediapipe into a variable.

In [18]:
# face bounder indices 
FACE_OVAL=[ 10, 338, 297, 332, 284, 251, 389, 356, 454, 323, 361, 288, 397, 365, 379, 378, 400, 377, 152, 148, 176, 149, 150, 136, 172, 58, 132, 93, 234, 127, 162, 21, 54, 103,67, 109]
 
# Left eyes indices 
LEFT_EYE =[ 362, 382, 381, 380, 374, 373, 390, 249, 263, 466, 388, 387, 386, 385,384, 398 ]
LEFT_EYEBROW =[ 336, 296, 334, 293, 300, 276, 283, 282, 295, 285 ]

# right eyes indices
RIGHT_EYE=[ 33, 7, 163, 144, 145, 153, 154, 155, 133, 173, 157, 158, 159, 160, 161 , 246 ]  
RIGHT_EYEBROW=[ 70, 63, 105, 66, 107, 55, 65, 52, 53, 46 ]

## Calculating blink rate (Euclidean distance).

In [19]:
# Blinking Ratio
def blinkRatio(img, landmarks, right_indices, left_indices):
    # Right eyes 
    # horizontal line 
    rh_right = landmarks[right_indices[0]]
    rh_left = landmarks[right_indices[8]]
    # vertical line 
    rv_top = landmarks[right_indices[12]]
    rv_bottom = landmarks[right_indices[4]]
    # draw lines on right eyes 
    # cv.line(img, rh_right, rh_left, utils.GREEN, 2)
    # cv.line(img, rv_top, rv_bottom, utils.WHITE, 2)

    # LEFT_EYE 
    # horizontal line 
    lh_right = landmarks[left_indices[0]]
    lh_left = landmarks[left_indices[8]]

    # vertical line 
    lv_top = landmarks[left_indices[12]]
    lv_bottom = landmarks[left_indices[4]]

    rhDistance = euclaideanDistance(rh_right, rh_left)
    rvDistance = euclaideanDistance(rv_top, rv_bottom)

    lvDistance = euclaideanDistance(lv_top, lv_bottom)
    lhDistance = euclaideanDistance(lh_right, lh_left)

    reRatio = rhDistance/rvDistance
    leRatio = lhDistance/lvDistance

    ratio = (reRatio+leRatio)/2
    return ratio

# Euclaidean distance
def euclaideanDistance(point, point1):
    x, y = point
    x1, y1 = point1
    distance = sqrt((x1 - x)**2 + (y1 - y)**2)
    if 1> distance:
        return 1
    else:
        return distance

# 03. Extract Position Landmarks (Keypoints Values) 

In [75]:
def extract_landmarks(img, results):
    resized_frame = cv2.resize(img, None, fx=1.5, fy=1.5, interpolation=cv2.INTER_CUBIC)
    mesh_coords = mesh_coord_detection(img, results)
    
    # extract face 478 keyponits
    face = np.array([[res.x, res.y, res.z] for res in results.multi_face_landmarks[0].landmark]).flatten() if results.multi_face_landmarks[0] else np.zeros(478*3)
    
    # extract right-eye 16 keypoints
    right_eye_coords = np.array([mesh_coords[p] for p in RIGHT_EYE]).flatten()  
    
    # extract left-eye 16 keypoints
    left_eye_coords = np.array([mesh_coords[p] for p in LEFT_EYE]).flatten()    
    
    # calculating eye ratio
    ratio = np.array(blinkRatio(resized_frame, mesh_coords, RIGHT_EYE, LEFT_EYE)).flatten()  
    
    # return all feature values
    return np.concatenate([face,right_eye_coords,left_eye_coords,ratio])


def mesh_coord_detection(img, results):
    img_height, img_width= img.shape[:2]
    print("img_height||img_width||img.shape||img.shape[0:2]:" ,img_height,img_width,img.shape,img.shape[:2])
    # list[(x,y), (x,y)....]
    mesh_coord = [(int(point.x * img_width), int(point.y * img_height)) for point in results.multi_face_landmarks[0].landmark]

    print("Mesh_Cord",mesh_coord)
    # returning the list of tuples for each landmarks 
    return mesh_coord

In [74]:
results.multi_face_landmarks[0].landmark

[x: 0.49131125
y: 0.6014309
z: -0.06534048
, x: 0.49962664
y: 0.5243
z: -0.10632838
, x: 0.496538
y: 0.5513625
z: -0.06053968
, x: 0.4858369
y: 0.4532977
z: -0.074504666
, x: 0.5009707
y: 0.50087005
z: -0.11111908
, x: 0.5018609
y: 0.4726799
z: -0.10085008
, x: 0.50319153
y: 0.40713954
z: -0.040939264
, x: 0.35825658
y: 0.40132952
z: 0.031422503
, x: 0.5048828
y: 0.3567778
z: -0.022277981
, x: 0.50635093
y: 0.32753524
z: -0.022688868
, x: 0.5116348
y: 0.22261247
z: 0.0105812745
, x: 0.49092302
y: 0.6093462
z: -0.06356657
, x: 0.4902354
y: 0.6178408
z: -0.05778535
, x: 0.4897065
y: 0.6235302
z: -0.04955308
, x: 0.48946238
y: 0.6522003
z: -0.046556856
, x: 0.48937765
y: 0.6599162
z: -0.050582852
, x: 0.48907635
y: 0.67033744
z: -0.055847555
, x: 0.48843136
y: 0.6826564
z: -0.054428365
, x: 0.48736164
y: 0.70104086
z: -0.038290437
, x: 0.49848345
y: 0.53749555
z: -0.09737066
, x: 0.48022613
y: 0.5383185
z: -0.07200787
, x: 0.3019504
y: 0.32776475
z: 0.12972441
, x: 0.41466296
y: 0.4218046

# 04. Setup Folder for Collection

In [26]:
DATA_PATH = os.path.join('ML_Data')         # Path for exported data, numpy arrays

actions = np.array(['true', 'lie'])       # Actions that we try to detect

no_sequences = 21                       # videos worth of data per action (True-02 vdos, Lie-02 Vdos)

sequence_length = 30              # Videos are going to be 30 frames in length

In [47]:
# Create Folders for save keypoints values

for action in actions:
    for sequence in range(no_sequences):
        try:
            os.makedirs(os.path.join(DATA_PATH, action, str(sequence)))
        except:
            pass

#  05. Collect Keypoints Values for Training and Testing

In [76]:
for action in actions:   # Loop through actions
    
    for sequence in range(no_sequences):          # Loop through sequences (videos)
        
        VDO_PATH = 'Datasets/' + action +'/' + str(sequence) + '/' + str(sequence) + '.mp4'  # /Datasets/true/0/0.mp4
        cap = cv2.VideoCapture(VDO_PATH)                # Read Video
        
        with mp.solutions.face_mesh.FaceMesh(                         # set mediapipe model
            max_num_faces =1,
            refine_landmarks = True,
            min_detection_confidence=0.5,
            min_tracking_confidence=0.5) as face_mesh:
            for frame_num in range(sequence_length):

                ret, frame = cap.read()                                # Read feed

                print("Processing Video Path:",VDO_PATH)                      # Processing Video Path:Datasets/true/0/0.mp4

                image, results = mediapipe_detection(frame, face_mesh)                # Make detection
    
                feature_values = extract_landmarks(image,results)                   # Extract face , left-eye , right-eye keypoints
            
                npy_path = os.path.join(DATA_PATH, action, str(sequence), str(frame_num)) # create export keypoints local path
            
                print("feature_valuess Shape:", feature_values.shape)                       # Keypoints Shape:(1499,) ---> (1434 + 32 + 32 + 1)
                
                np.save(npy_path, feature_values)                                   # Save Keypoints values
                
                

            cap.release()     # Release feed
            
            cv2.waitKey(1)    # wait for 1 Secound
            
            print("____________Finish__________________")                  

Processing Video Path: Datasets/true/0/0.mp4
img_height||img_width||img.shape||img.shape[0:2]: 306 324 (306, 324, 3) (306, 324)
Mesh_Cord [(145, 194), (143, 176), (144, 182), (140, 159), (143, 170), (144, 163), (145, 148), (111, 149), (145, 135), (145, 128), (146, 104), (146, 196), (146, 198), (146, 199), (146, 209), (146, 210), (146, 213), (146, 215), (144, 219), (144, 179), (139, 179), (96, 134), (124, 154), (119, 154), (115, 154), (109, 151), (129, 152), (118, 138), (124, 138), (113, 139), (110, 141), (105, 155), (126, 228), (110, 148), (93, 156), (101, 152), (120, 174), (138, 194), (139, 198), (131, 196), (127, 199), (134, 199), (129, 201), (121, 208), (139, 176), (139, 170), (103, 136), (130, 161), (128, 175), (128, 173), (106, 174), (139, 164), (114, 129), (108, 131), (101, 123), (135, 132), (129, 140), (118, 202), (99, 208), (132, 179), (136, 180), (122, 204), (123, 204), (106, 128), (128, 178), (123, 129), (123, 124), (119, 108), (103, 126), (121, 117), (101, 135), (98, 135), (

img_height||img_width||img.shape||img.shape[0:2]: 306 324 (306, 324, 3) (306, 324)
Mesh_Cord [(145, 194), (145, 175), (145, 182), (141, 158), (145, 169), (145, 162), (146, 147), (111, 149), (146, 135), (146, 127), (147, 101), (145, 197), (145, 199), (145, 200), (145, 208), (145, 210), (145, 213), (146, 216), (145, 220), (145, 179), (141, 179), (96, 132), (124, 154), (119, 154), (115, 154), (109, 151), (129, 152), (118, 137), (124, 137), (113, 138), (109, 140), (105, 154), (127, 229), (109, 148), (93, 155), (100, 151), (121, 174), (138, 194), (139, 199), (131, 197), (127, 199), (133, 200), (129, 202), (122, 209), (141, 175), (140, 170), (103, 136), (131, 161), (129, 175), (129, 173), (106, 175), (141, 163), (114, 128), (107, 131), (100, 121), (136, 133), (129, 140), (118, 203), (98, 209), (133, 178), (137, 180), (122, 205), (124, 205), (105, 128), (129, 178), (124, 129), (123, 124), (119, 105), (103, 124), (122, 114), (101, 134), (98, 133), (138, 197), (132, 199), (128, 201), (134, 180)

Processing Video Path: Datasets/true/0/0.mp4
img_height||img_width||img.shape||img.shape[0:2]: 306 324 (306, 324, 3) (306, 324)
Mesh_Cord [(151, 194), (153, 173), (152, 181), (149, 157), (153, 168), (153, 161), (154, 146), (118, 146), (155, 135), (155, 128), (157, 101), (151, 197), (151, 199), (151, 200), (151, 200), (151, 202), (151, 205), (151, 208), (150, 215), (152, 177), (148, 177), (102, 129), (131, 151), (126, 151), (122, 151), (116, 148), (136, 150), (126, 135), (131, 136), (120, 136), (116, 138), (112, 152), (131, 225), (116, 145), (99, 153), (107, 148), (127, 172), (145, 194), (146, 199), (139, 196), (134, 199), (141, 199), (136, 201), (127, 207), (149, 173), (148, 168), (111, 133), (138, 159), (136, 174), (136, 171), (113, 172), (149, 162), (123, 127), (115, 129), (108, 118), (144, 133), (136, 138), (124, 201), (101, 207), (140, 177), (144, 179), (129, 203), (130, 203), (113, 126), (136, 176), (132, 128), (132, 124), (129, 103), (111, 122), (131, 113), (108, 132), (105, 131)

Processing Video Path: Datasets/true/0/0.mp4
img_height||img_width||img.shape||img.shape[0:2]: 306 324 (306, 324, 3) (306, 324)
Mesh_Cord [(153, 191), (155, 172), (155, 179), (153, 155), (156, 166), (156, 159), (158, 145), (122, 145), (158, 134), (159, 127), (161, 101), (153, 193), (153, 195), (153, 197), (153, 202), (153, 204), (153, 207), (152, 210), (153, 216), (155, 175), (151, 176), (107, 128), (135, 150), (130, 151), (126, 150), (120, 147), (140, 149), (130, 134), (135, 135), (124, 135), (120, 137), (116, 151), (134, 224), (120, 144), (103, 152), (111, 147), (131, 171), (147, 190), (148, 196), (141, 193), (137, 197), (143, 197), (140, 199), (131, 206), (151, 171), (151, 166), (114, 132), (142, 158), (140, 172), (139, 169), (116, 171), (152, 160), (126, 126), (119, 128), (113, 118), (148, 132), (140, 138), (127, 200), (104, 205), (143, 175), (147, 177), (134, 203), (135, 202), (117, 125), (139, 174), (136, 127), (135, 123), (133, 103), (116, 122), (135, 113), (112, 131), (110, 130

feature_valuess Shape: (1499,)
Processing Video Path: Datasets/true/1/1.mp4
img_height||img_width||img.shape||img.shape[0:2]: 398 430 (398, 430, 3) (398, 430)
Mesh_Cord [(225, 279), (225, 252), (225, 261), (219, 224), (225, 243), (225, 231), (226, 206), (168, 209), (226, 190), (227, 179), (228, 136), (224, 282), (224, 286), (224, 288), (224, 288), (224, 292), (223, 296), (223, 301), (223, 311), (225, 257), (216, 256), (139, 180), (191, 214), (183, 215), (175, 215), (164, 212), (198, 212), (178, 194), (188, 195), (170, 195), (164, 198), (157, 217), (192, 329), (165, 208), (135, 216), (148, 212), (184, 246), (215, 277), (215, 285), (205, 280), (198, 283), (208, 285), (202, 286), (186, 297), (218, 252), (217, 243), (151, 191), (202, 225), (198, 249), (197, 244), (160, 246), (218, 232), (171, 181), (159, 184), (147, 163), (208, 188), (196, 197), (180, 290), (141, 298), (204, 254), (211, 256), (191, 288), (193, 288), (154, 179), (197, 252), (187, 182), (185, 175), (181, 141), (153, 171), (1

...

____________Finish__________________
Processing Video Path: Datasets/lie/20/20.mp4
img_height||img_width||img.shape||img.shape[0:2]: 344 364 (344, 364, 3) (344, 364)
Mesh_Cord [(176, 202), (176, 178), (175, 187), (171, 154), (177, 171), (177, 161), (178, 138), (129, 134), (178, 121), (179, 111), (181, 79), (175, 205), (175, 209), (175, 211), (174, 220), (174, 223), (174, 226), (174, 231), (172, 237), (176, 183), (169, 182), (106, 109), (148, 141), (141, 142), (134, 141), (126, 136), (154, 140), (139, 118), (147, 119), (131, 119), (126, 122), (120, 141), (145, 246), (127, 131), (100, 140), (113, 136), (141, 172), (167, 201), (167, 209), (157, 205), (150, 208), (159, 210), (153, 212), (140, 221), (170, 178), (170, 170), (117, 116), (156, 154), (153, 176), (153, 172), (121, 171), (170, 161), (133, 108), (124, 111), (114, 96), (164, 116), (154, 123), (136, 213), (103, 211), (158, 181), (164, 183), (142, 215), (145, 215), (120, 106), (153, 180), (146, 109), (145, 103), (142, 80), (118, 102)

Processing Video Path: Datasets/lie/20/20.mp4
img_height||img_width||img.shape||img.shape[0:2]: 344 364 (344, 364, 3) (344, 364)
Mesh_Cord [(177, 213), (181, 187), (180, 196), (176, 161), (182, 179), (182, 169), (183, 145), (132, 141), (183, 127), (184, 117), (186, 81), (177, 217), (177, 220), (177, 223), (177, 223), (176, 227), (176, 231), (176, 235), (176, 241), (181, 191), (173, 191), (108, 113), (150, 148), (143, 148), (137, 148), (128, 143), (156, 146), (142, 126), (150, 128), (135, 127), (130, 130), (122, 148), (148, 253), (129, 139), (103, 146), (115, 143), (145, 180), (168, 212), (169, 220), (159, 215), (152, 218), (162, 221), (156, 222), (143, 228), (175, 187), (175, 179), (121, 123), (160, 162), (157, 185), (157, 180), (124, 178), (176, 169), (138, 115), (128, 117), (116, 100), (168, 124), (157, 131), (138, 221), (106, 218), (162, 189), (168, 192), (145, 224), (147, 224), (125, 113), (157, 188), (151, 117), (150, 111), (146, 82), (121, 106), (150, 96), (117, 120), (113, 117),

feature_valuess Shape: (1499,)
Processing Video Path: Datasets/lie/20/20.mp4
img_height||img_width||img.shape||img.shape[0:2]: 344 364 (344, 364, 3) (344, 364)
Mesh_Cord [(177, 212), (179, 184), (178, 194), (175, 160), (180, 176), (180, 166), (181, 143), (129, 140), (182, 125), (182, 115), (184, 79), (177, 214), (177, 217), (177, 219), (177, 230), (177, 233), (176, 237), (176, 241), (174, 248), (179, 189), (173, 189), (107, 114), (149, 149), (142, 149), (135, 148), (126, 143), (156, 147), (140, 125), (149, 127), (132, 126), (127, 129), (121, 149), (148, 256), (127, 138), (102, 147), (114, 144), (144, 180), (169, 210), (170, 217), (160, 214), (155, 219), (163, 219), (159, 221), (143, 231), (174, 184), (173, 176), (118, 123), (159, 161), (157, 183), (157, 179), (123, 179), (174, 167), (135, 115), (125, 117), (115, 100), (167, 123), (156, 131), (139, 223), (106, 221), (162, 188), (168, 190), (149, 227), (151, 227), (122, 113), (156, 187), (148, 116), (147, 110), (145, 81), (120, 106), (14

feature_valuess Shape: (1499,)
Processing Video Path: Datasets/lie/20/20.mp4
img_height||img_width||img.shape||img.shape[0:2]: 344 364 (344, 364, 3) (344, 364)
Mesh_Cord [(179, 204), (182, 178), (181, 187), (177, 153), (183, 170), (183, 160), (183, 138), (130, 136), (183, 121), (184, 111), (185, 75), (179, 207), (179, 209), (179, 211), (179, 222), (179, 225), (178, 228), (178, 233), (178, 239), (182, 182), (175, 183), (109, 111), (151, 143), (144, 143), (137, 143), (128, 139), (157, 141), (141, 119), (150, 121), (134, 120), (128, 124), (122, 144), (151, 249), (128, 133), (104, 144), (115, 139), (146, 174), (170, 203), (171, 210), (161, 207), (154, 211), (164, 211), (158, 214), (145, 224), (176, 177), (176, 170), (121, 118), (161, 155), (159, 177), (158, 173), (125, 174), (176, 161), (138, 110), (128, 112), (117, 97), (169, 118), (157, 125), (141, 216), (108, 217), (164, 181), (170, 184), (148, 220), (150, 219), (124, 108), (158, 181), (151, 111), (150, 105), (146, 78), (122, 103), (150

img_height||img_width||img.shape||img.shape[0:2]: 344 364 (344, 364, 3) (344, 364)
Mesh_Cord [(178, 205), (181, 179), (180, 188), (176, 155), (182, 171), (182, 161), (183, 139), (130, 137), (183, 121), (184, 111), (185, 76), (178, 208), (177, 211), (177, 213), (177, 223), (177, 226), (177, 229), (177, 234), (177, 240), (181, 184), (174, 184), (109, 112), (150, 144), (143, 144), (136, 144), (127, 140), (156, 142), (141, 120), (150, 122), (133, 122), (128, 125), (122, 145), (150, 250), (127, 134), (104, 144), (115, 140), (145, 175), (169, 204), (169, 211), (159, 208), (153, 213), (162, 213), (157, 215), (145, 225), (175, 179), (175, 171), (120, 119), (160, 156), (158, 178), (158, 174), (125, 175), (176, 162), (137, 111), (127, 113), (117, 97), (168, 119), (157, 126), (140, 217), (108, 218), (163, 183), (169, 185), (147, 221), (149, 221), (124, 109), (158, 182), (151, 112), (150, 106), (146, 78), (121, 103), (150, 92), (117, 117), (113, 115), (169, 208), (161, 211), (155, 214), (165, 184)

# 6. Preprocess Data and Create Labels and Features

In [34]:
from sklearn.model_selection import train_test_split # Scikit-learn for our evaluation metrics
from tensorflow.keras.utils import to_categorical   # Converting Data (Encoded)

In [35]:
label_map = {label:num for num, label in enumerate(actions)}  # Actions Label Map  {'true': 0, 'lie': 1} 

In [36]:
sequences, labels = [], []                # like : Features(X) Data , labels(Y) Data
for action in actions:              
    for sequence in range(no_sequences):  
        values = []                       # Save all of diff.frames paricular sequence
        for frame_num in range(sequence_length):
            res = np.load(os.path.join(DATA_PATH, action, str(sequence), "{}.npy".format(frame_num)))  # load np array
            values.append(res)                # Append all res 
        sequences.append(values)             # Append all values
        labels.append(label_map[action])   # Append all actions on labels

In [110]:
X_train.shape

(39, 50, 1498)

In [37]:
X = np.array(sequences)  # sequences
y = to_categorical(labels).astype(int)  # labels

# Train & Testing Partition
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.05) 

In [112]:
# X.shape : (42, 30, 1499)  -----> ( Sequences(videos) , framers per vdo, keypoints shape [(478 * 3) + (32 * 2) + 1] )
# y.shape : (42, 2) -------->   ( Sequences(videos), labels[actions] )

# X_train.shape : (39, 30, 1499) 
# X_test.shape : (3, 30, 1499)

# y_train.shape : (39, 2) 
# y_test.shape : (3, 2) 

In [39]:
X.shape

(42, 60, 1499)

In [40]:
y.shape

(42, 2)

In [41]:
X_train.shape

(39, 60, 1499)

In [43]:
X_test.shape

(3, 60, 1499)

In [44]:
y_train.shape

(39, 2)

In [45]:
y_test.shape

(3, 2)

# 7. Build and Train LSTM Neural Network

In [46]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.callbacks import TensorBoard

In [47]:
log_dir = os.path.join('Logs')
tb_callback = TensorBoard(log_dir=log_dir)

In [48]:
model = Sequential()
model.add(LSTM(64, return_sequences=True, activation='relu', input_shape=(30,1499)))
model.add(LSTM(128, return_sequences=True, activation='relu'))
model.add(LSTM(64, return_sequences=False, activation='relu'))
model.add(Dense(64, activation='relu'))
model.add(Dense(32, activation='relu'))
model.add(Dense(actions.shape[0], activation='softmax'))

In [49]:
actions.shape[0]

2

In [50]:
res = [.7, 0.2, 0.1]

In [51]:
actions[np.argmax(res)]

'true'

In [52]:
model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['categorical_accuracy'])

In [53]:
model.fit(X_train, y_train, epochs=50, callbacks=[tb_callback])

Epoch 1/50
2/2 [==============================] - 9s 5s/step - loss: 733.9969 - categorical_accuracy: 0.4359
Epoch 2/50
2/2 [==============================] - 0s 114ms/step - loss: 2260.3418 - categorical_accuracy: 0.2308
Epoch 3/50
2/2 [==============================] - 0s 126ms/step - loss: 722.3153 - categorical_accuracy: 0.6410
Epoch 4/50
2/2 [==============================] - 0s 132ms/step - loss: 2493.0347 - categorical_accuracy: 0.3846
Epoch 5/50
2/2 [==============================] - 0s 125ms/step - loss: 615.6875 - categorical_accuracy: 0.5385
Epoch 6/50
2/2 [==============================] - 0s 118ms/step - loss: 711.9672 - categorical_accuracy: 0.2821
Epoch 7/50
2/2 [==============================] - 0s 121ms/step - loss: 321.9678 - categorical_accuracy: 0.4872
Epoch 8/50
2/2 [==============================] - 0s 118ms/step - loss: 409.9810 - categorical_accuracy: 0.5897
Epoch 9/50
2/2 [==============================] - 0s 120ms/step - loss: 753.7300 - categorical_accuracy: 

In [24]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm (LSTM)                  (None, 30, 64)            400384    
_________________________________________________________________
lstm_1 (LSTM)                (None, 30, 128)           98816     
_________________________________________________________________
lstm_2 (LSTM)                (None, 64)                49408     
_________________________________________________________________
dense (Dense)                (None, 64)                4160      
_________________________________________________________________
dense_1 (Dense)              (None, 32)                2080      
_________________________________________________________________
dense_2 (Dense)              (None, 2)                 66        
Total params: 554,914
Trainable params: 554,914
Non-trainable params: 0
__________________________________________________

# 8. Make Predictions

In [140]:
res = model.predict(X_test)

In [141]:
res

array([[0.0000000e+00, 1.0000000e+00],
       [0.0000000e+00, 1.0000000e+00],
       [2.7822821e-06, 9.9999726e-01]], dtype=float32)

In [142]:
np.sum(res[0])

1.0

In [143]:
actions[np.argmax(res[0])]

'lie'

In [144]:
y_test

array([[0, 1],
       [1, 0],
       [1, 0]])

In [145]:
actions[np.argmax(y_test[0])]

'lie'

# 9. Save Weights

In [146]:
model.save('action.h5')

In [33]:
del model

In [25]:
model.load_weights('action.h5')

# 10. Evaluation using Confusion Matrix and Accuracy

In [26]:
from sklearn.metrics import multilabel_confusion_matrix, accuracy_score

In [27]:
yhat = model.predict(X_test)

In [28]:
ytrue = np.argmax(y_test, axis=1).tolist()
yhat = np.argmax(yhat, axis=1).tolist()

In [29]:
plt.figure(figsize=(18,18))

<Figure size 1296x1296 with 0 Axes>

<Figure size 1296x1296 with 0 Axes>

In [151]:
ytrue

[1, 0, 0]

In [152]:
multilabel_confusion_matrix(ytrue, yhat)

array([[[1, 0],
        [2, 0]],

       [[0, 2],
        [0, 1]]], dtype=int64)

In [43]:
multilabel_confusion_matrix??

In [153]:
accuracy_score(ytrue, yhat)

0.3333333333333333

# 11. Test in Real Time

In [54]:
colors = [(245,117,16), (117,245,16), (16,117,245)]
def prob_viz(res, actions, input_frame, colors):
    output_frame = input_frame.copy()
    for num, prob in enumerate(res):
        cv2.rectangle(output_frame, (0,60+num*40), (int(prob*100), 90+num*40), colors[num], -1)
        cv2.putText(output_frame, actions[num], (0, 85+num*40), cv2.FONT_HERSHEY_SIMPLEX, 1, (255,255,255), 2, cv2.LINE_AA)
        
    return output_frame

In [55]:
def draw_landmarks(image,face_landmarks):
    # Draw face connections
    mp_drawing.draw_landmarks(
            image= image,
            landmark_list= face_landmarks,
            connections= mp_face_mesh.FACEMESH_TESSELATION,
            landmark_drawing_spec= None,
            connection_drawing_spec=mp_drawing_styles.get_default_face_mesh_tesselation_style())
    
    # Draw face countours (FACEMESH_CONTOURS = frozenset().union(*[FACEMESH_LIPS, FACEMESH_LEFT_EYE, FACEMESH_LEFT_EYEBROW, FACEME) connections
    mp_drawing.draw_landmarks(
            image= image,
            landmark_list= face_landmarks,
            connections= mp_face_mesh.FACEMESH_CONTOURS,
            landmark_drawing_spec= None,
            connection_drawing_spec= mp_drawing_styles.get_default_face_mesh_contours_style())
    
    # Draw eye iris ( FACEMESH_IRISES = frozenset().union(*[FACEMESH_LEFT_IRIS, FACEMESH_RIGHT_IRIS]) ) connections
    mp_drawing.draw_landmarks(
            image= image,
            landmark_list= face_landmarks,
            connections= mp_face_mesh.FACEMESH_IRISES,
            landmark_drawing_spec= None,
            connection_drawing_spec= mp_drawing_styles.get_default_face_mesh_iris_connections_style())

In [57]:
# 1. New detection variables
sequence = []
sentence = []
threshold = 0.8

cap = cv2.VideoCapture(0)
# Set mediapipe model 
with mp_face_mesh.FaceMesh(min_detection_confidence=0.5, min_tracking_confidence=0.5) as face_mesh:
    while cap.isOpened():

        # Read feed
        ret, frame = cap.read()

        # Make detections
        image, results = mediapipe_detection(frame, face_mesh)
        print(results)
        
        # Draw landmarks
#         draw_landmarks(image, results)
        
        # 2. Prediction logic
        keypoints = extract_landmarks(image , results)
#         sequence.insert(0,keypoints)
#         sequence = sequence[:30]
        sequence.append(keypoints)
        sequence = sequence[-30:]
        
        if len(sequence) == 30:
            res = model.predict(np.expand_dims(sequence, axis=0))[0]
            print(actions[np.argmax(res)])
            
            
        #3. Viz logic
            if res[np.argmax(res)] > threshold: 
                if len(sentence) > 0: 
                    if actions[np.argmax(res)] != sentence[-1]:
                        sentence.append(actions[np.argmax(res)])
                else:
                    sentence.append(actions[np.argmax(res)])

            if len(sentence) > 5: 
                sentence = sentence[-5:]

            # Viz probabilities
            image = prob_viz(res, actions, image, colors)
            
        cv2.rectangle(image, (0,0), (640, 40), (245, 117, 16), -1)
        cv2.putText(image, ' '.join(sentence), (3,30), 
        cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2, cv2.LINE_AA)
        
        # Show to screen
        cv2.imshow('Lie Detection', image)

        # Break gracefully
        if cv2.waitKey(10) & 0xFF == ord('q'):
            break
    cap.release()
    cv2.destroyAllWindows()

<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.soluti

ValueError: in user code:

    C:\Anaconda\lib\site-packages\tensorflow\python\keras\engine\training.py:1569 predict_function  *
        return step_function(self, iterator)
    C:\Anaconda\lib\site-packages\tensorflow\python\keras\engine\training.py:1559 step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    C:\Anaconda\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:1285 run
        return self._extended.call_for_each_replica(fn, args=args, kwargs=kwargs)
    C:\Anaconda\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:2833 call_for_each_replica
        return self._call_for_each_replica(fn, args, kwargs)
    C:\Anaconda\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:3608 _call_for_each_replica
        return fn(*args, **kwargs)
    C:\Anaconda\lib\site-packages\tensorflow\python\keras\engine\training.py:1552 run_step  **
        outputs = model.predict_step(data)
    C:\Anaconda\lib\site-packag

In [2]:
cap.release()
cv2.destroyAllWindows()

NameError: name 'cap' is not defined